In [2]:
import time
import math
import numpy as np
import torch
from torch import nn,optim
import torch.nn.functional as F
import random
import zipfile

In [3]:
def load_data_jay_lyrics():
    with zipfile.ZipFile(r'F:\study\ml\ebooks3\6\jaychou_lyrics.txt.zip') as zin:
        with zin.open('jaychou_lyrics.txt') as f:
            corpus_chars=f.read().decode('utf-8')
    corpus_chars=corpus_chars.replace('\n',' ').replace('\r',' ')
    corpus_chars=corpus_chars[0:10000]
    idx_to_char=list(set(corpus_chars))
    char_to_idx=dict([( char,i ) for i , char in enumerate(idx_to_char)])
    vocab_size=len(char_to_idx)
    corpus_indices=[char_to_idx[char] for char in corpus_chars]
    return corpus_indices, char_to_idx, idx_to_char, vocab_size

In [4]:
corpus_indices, char_to_idx, idx_to_char, vocab_size=load_data_jay_lyrics()

In [5]:
def one_hot(x,n_class,dtype=torch.float32):
    x=x.long()
    res=torch.zeros(x.shape[0],n_class,dtype=dtype,device=x.device)
    res.scatter_(1,x.view(-1,1),1)
    return res

In [6]:
def to_onehot(X,n_class):
    return [one_hot(X[:,i],n_class) for i in range(X.shape[1])]

In [7]:
X=torch.arange(10).view(2,5)
X

tensor([[0, 1, 2, 3, 4],
        [5, 6, 7, 8, 9]])

In [8]:
vocab_size

1027

In [9]:
inputs=to_onehot(X,vocab_size)
print(len(inputs),inputs[0].shape)

5 torch.Size([2, 1027])


In [10]:
inputs

[tensor([[1., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]]),
 tensor([[0., 1., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]]),
 tensor([[0., 0., 1.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]]),
 tensor([[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]]),
 tensor([[0., 0., 0.,  ..., 0., 0., 0.],
         [0., 0., 0.,  ..., 0., 0., 0.]])]

In [11]:
 [X[:,i] for i in range(X.shape[1])]

[tensor([0, 5]),
 tensor([1, 6]),
 tensor([2, 7]),
 tensor([3, 8]),
 tensor([4, 9])]

In [12]:
one_hot(torch.Tensor([0, 5]),1027)

tensor([[1., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])

In [13]:
num_inputs,num_hiddens,num_outputs=vocab_size,256,vocab_size

In [14]:
def get_params():
    def _one(shape):
        ts=torch.tensor(np.random.normal(0,0.01,size=shape),dtype=torch.float32)
        return torch.nn.Parameter(ts,requires_grad=True)
    
    W_xh=_one((num_inputs,num_hiddens))
    W_hh=_one((num_hiddens,num_hiddens))
    b_h=torch.nn.Parameter(torch.zeros(num_hiddens,requires_grad=True))
    W_hq=_one((num_hiddens,num_outputs))
    b_q=torch.nn.Parameter(torch.zeros(num_outputs,requires_grad=True))
    return nn.ParameterList([W_xh,W_hh,b_h,W_hq,b_q])
    

In [15]:
def init_rnn_state(batch_size,num_hiddens,device):
    return (torch.zeros((batch_size,num_hiddens),device=device),)

In [34]:
def rnn(inputs,state,params):
    W_xh,W_hh,b_h,W_hq,b_q=params
    H,=state
    outputs=[]
    for X in inputs:
        
        print('X shape : ',X.shape)
        # 1*1027 ,1027*256 + 1*256 ,256 *1 = 1*256
        H=torch.tanh(torch.matmul(X,W_xh)+torch.matmul(H,W_hh)+b_h)
        print('H.shape : ',H.shape)
        # 1*256 * 256*1027 = 1*1027
        Y=torch.matmul(H,W_hq)+b_q
        outputs.append(Y)
    return outputs,(H,)

In [35]:
device='cpu'
state=init_rnn_state(X.shape[0],num_hiddens,device)
inputs=to_onehot(X.to(device),vocab_size)
params=get_params()
outputs,state_new=rnn(inputs,state,params)
print(len(outputs),outputs[0].shape,state_new[0].shape)

X shape :  torch.Size([2, 1027])
H.shape :  torch.Size([2, 256])
X shape :  torch.Size([2, 1027])
H.shape :  torch.Size([2, 256])
X shape :  torch.Size([2, 1027])
H.shape :  torch.Size([2, 256])
X shape :  torch.Size([2, 1027])
H.shape :  torch.Size([2, 256])
X shape :  torch.Size([2, 1027])
H.shape :  torch.Size([2, 256])
5 torch.Size([2, 1027]) torch.Size([2, 256])


In [38]:
def predict_rnn(prefix,num_chars,rnn,params,init_rnn_state,num_hiddens,vocab_size,device,idx_to_char,char_to_idx):
    state=init_rnn_state(1,num_hiddens,device)
    output=[char_to_idx[prefix[0]]]
    for t in range(num_chars+len(prefix) -1):
        print('before X :',torch.tensor([[output[-1]]],device=device))
        X= to_onehot(torch.tensor([[output[-1]]],device=device),vocab_size)
        print('X Input shape : ',len(X))
        (Y,state)=rnn(X,state,params)
        print('Y shape :',len(Y))
        print('Y :',Y)
        if t<len(prefix) -1:
            output.append(char_to_idx[prefix[t+1]])
        else:
            output.append(int(Y[0].argmax(dim=1).item()))
    return ''.join([idx_to_char[i] for i in output])

In [39]:
predict_rnn('分开',10,rnn,params,init_rnn_state,num_hiddens,vocab_size,device,idx_to_char,char_to_idx)

before X : tensor([[187]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[ 0.0007,  0.0023, -0.0002,  ..., -0.0011, -0.0032, -0.0014]],
       grad_fn=<AddBackward0>)]
before X : tensor([[756]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[ 0.0042, -0.0004,  0.0020,  ..., -0.0016,  0.0044,  0.0024]],
       grad_fn=<AddBackward0>)]
before X : tensor([[399]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[ 0.0031,  0.0019,  0.0023,  ..., -0.0012,  0.0020,  0.0015]],
       grad_fn=<AddBackward0>)]
before X : tensor([[46]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[-0.0009,  0.0001, -0.0013,  ..., -0.0015,  0.0004,  0.0008]],
       grad_fn=<AddBackward0>)]
before X : tensor([[725]])
X Input shape :  1
X shape :  torch.Size([1, 1027]

'分开撒弄点照果望拉离性失'

In [76]:
char_to_idx['分']

414

In [42]:
def grad_clipping(params,theta,device):
    norm = torch.tensor([0.0],device=device)
    for param in params:
        norm +=(param.grad.data **2).sum()
    norm=norm.sqrt().item()
    if norm > theta:
        for param in params:
            param.grad.data *= (theta / norm)

In [56]:
def data_iter_random(corpus_indices,batch_size,num_steps):
    num_examples=(len(corpus_indices)-1)//num_steps
    num_epoch=num_examples //batch_size
    example_indices=list(range(num_examples))
    random.shuffle(example_indices)
    
    def _data(pos):
        return corpus_indices[pos:pos+num_steps]
    
    for i in range(num_epoch):
        i=i*batch_size
        batch_indices=example_indices[i:i+batch_size]
        X=[_data(j*num_steps) for j in batch_indices]
        Y=[_data(j*num_steps+1) for j in batch_indices]
        yield torch.Tensor(X),torch.Tensor(Y)

In [57]:
def data_iter_consecutive(corpus_indices,batch_size,num_steps,device=None):
    if device is None:
        device=torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    corpus_indices=torch.tensor(corpus_indices,dtype=torch.float32,device=device)
    data_len=len(corpus_indices)
    batch_len=data_len//batch_size
    indices=corpus_indices[0:batch_size*batch_len].view(batch_size,batch_len)
    epoch_size=(batch_len-1) // num_steps
    for i in range(epoch_size):
        i=i*num_steps
        X=indices[:,i:i+num_steps]
        Y=indices[:,i+1:i+num_steps+1]
        yield X,Y

In [58]:
def sgd(params,lr,batch_size):
    for param in params:
        param.data -= lr * param.grad / batch_size

In [96]:
def train_and_predict_rnn(rnn, get_params, init_run_state, num_hiddens,
                          vocab_size, corpus_indices, idx_to_char, 
                          char_to_idx,
                          is_random_iter, num_epochs,num_steps, lr, clipping_theta,
                          batch_size, pred_period, pred_len, prefixes):
    if is_random_iter:
        data_iter_fn = data_iter_random
    else:
        data_iter_fn = data_iter_consecutive

    params = get_params()
    loss = nn.CrossEntropyLoss()

    for epoch in range(num_epochs):
        if not is_random_iter:
            state = init_rnn_state(batch_size, num_hiddens)
        l_sum, n, start = 0.0, 0, time.time()
        data_iter = data_iter_fn(corpus_indices, batch_size, num_steps)
        for X, Y in data_iter:
            if is_random_iter:
                state = init_rnn_state(batch_size, num_hiddens,device)
            else:
                for s in state:
                    s.detach_()
#             print('----')
#             print('X : ',X)
            print('X shape : ',X.shape)
            inputs = to_onehot(X, vocab_size)
            (outputs, state) = rnn(inputs, state, params)
            #print()
            outputs = torch.cat(outputs, dim=0)
            y = torch.transpose(Y, 0, 1).contiguous().view(-1)
            l = loss(outputs, y.long())

            if params[0].grad is not None:
                for param in params:
                    param.grad.data.zero_()
            l.backward()
            grad_clipping(params, clipping_theta,device)
            sgd(params, lr, 1)
            l_sum += l.item() * y.shape[0]
            n += y.shape[0]

        if (epoch + 1) % pred_period == 0:
            print('epoch %d,perplexity %f,time %.2f sec' %
                  (epoch + 1, math.exp(l_sum / n), time.time() - start))
            for prefix in prefixes:
                print(
                    ' -',
                    predict_rnn(prefix, pred_len, rnn, params, init_run_state,
                                num_hiddens, vocab_size, device ,idx_to_char,
                                char_to_idx))

In [97]:
num_epochs,num_steps,batch_size,lr,clipping_theta=250,35,32,1e2,1e-2
pred_period,pred_len,prefixes=50,50,['分开','不分开']

In [98]:
a=data_iter_random(corpus_indices, batch_size, num_steps)

In [99]:
train_and_predict_rnn(rnn,get_params,init_rnn_state,num_hiddens,vocab_size,
                     corpus_indices,idx_to_char,char_to_idx,True,
                     num_epochs,num_steps,lr,clipping_theta,batch_size,pred_period,
                     pred_len,prefixes)

X shape :  torch.Size([32, 35])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 102

X shape :  torch.Size([32, 35])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 102

X shape :  torch.Size([32, 35])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 102

X shape :  torch.Size([32, 35])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 102

X shape :  torch.Size([32, 35])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 102

...

X shape :  torch.Size([32, 35])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 102

H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 35])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256

X shape :  torch.Size([32, 35])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 1027])
H.shape :  torch.Size([32, 256])
X shape :  torch.Size([32, 102

H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[ 2.5942, -2.5945,  1.0257,  ...,  5.0181,  3.4388,  3.8035]],
       grad_fn=<AddBackward0>)]
before X : tensor([[262]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[ 0.6887, -4.0398,  0.3085,  ...,  3.0820,  1.3996, -0.3691]],
       grad_fn=<AddBackward0>)]
before X : tensor([[938]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[-1.7236, -2.7368, -2.7362,  ...,  3.5112,  5.2974,  0.4593]],
       grad_fn=<AddBackward0>)]
before X : tensor([[935]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[-5.0782,  2.4357,  1.7499,  ..., -2.1035,  5.9675, -1.1619]],
       grad_fn=<AddBackward0>)]
before X : tensor([[692]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[ 2.5630, -0.5206, 

before X : tensor([[612]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[3.7540, 3.7349, 3.1552,  ..., 1.4309, 7.5464, 2.4041]],
       grad_fn=<AddBackward0>)]
before X : tensor([[498]])
X Input shape :  1
X shape :  torch.Size([1, 1027])
H.shape :  torch.Size([1, 256])
Y shape : 1
Y : [tensor([[-0.9201, -0.5243, -0.0461,  ...,  4.1242,  1.2009, -1.1318]],
       grad_fn=<AddBackward0>)]
 - 不分开吗 我叫你爸 你打我妈 这样对吗干嘛这样 何必让酒牵鼻子走 瞎 说午险飞阳 周什么我的证  我 你的
